This exercise is based on Menczer et al **A First Couse in Network Science** which can be accessed [here](https://github.com/CambridgeUniversityPress/FirstCourseNetworkScience/blob/master/tutorials/Chapter%202%20Tutorial.ipynb).

In [1]:
!pip install nxviz

In [2]:
import networkx as nx
import matplotlib.pyplot as plt
import nxviz

# 1. Dataset: Brazil air traffic network

This repository contains several example network datasets. Among these is a network of Brazil air travel routes:

In [3]:
G = nx.read_graphml('/content/air_traffic.graphml')

In [4]:
# Filter to Brazil
nodesBrazil = [node for node, data in G.nodes(data=True) if data['country']=='BRASIL']
B = nx.subgraph(G, nodesBrazil)

The nodes in this graph are airports, represented by their [IATA codes](https://en.wikipedia.org/wiki/List_of_airports_by_IATA_code:_A); two nodes are connected with an edge if there is a scheduled flight directly connecting these two airports. We'll assume this graph to be undirected since a flight in one direction usually means there is a return flight.

Thus this graph has edges
```
[('HOM', 'ANC'), ('BGM', 'PHL'), ('BGM', 'IAD'), ...]
```
where ANC is Anchorage, IAD is Washington Dulles, etc.

These nodes also have **attributes** associated with them, containing additional information about the airports:

In [5]:
B.nodes['SBCF']

{'country': 'BRASIL',
 'latitude': -19.624444,
 'longitude': -43.971944,
 'name': 'CONFINS'}

Node attributes are stored as a dictionary, so the values can be accessed individually as such:

In [6]:
B.nodes['SBCF']['name']

'CONFINS'

It is possible to note the number of nodes and edges.

In [7]:
number_of_nodes_B = B.number_of_nodes()
number_of_nodes_G = G.number_of_nodes()

print('Number of nodes (B):', number_of_nodes_B)
print('Number of nodes (G):', number_of_nodes_G)
print('percent:', number_of_nodes_B / number_of_nodes_G)

Number of nodes (B): 495
Number of nodes (G): 1082
percent: 0.45748613678373384


In [8]:
number_of_edges_B = B.number_of_edges()
number_of_edges_G = G.number_of_edges()

print('Number of edges (B):', number_of_edges_B)
print('Number of edges (G):', number_of_edges_G)
print('percent:', number_of_edges_B / number_of_edges_G)

Number of edges (B): 4594
Number of edges (G): 9920
percent: 0.46310483870967745


# EXERCISE 1

Is there a direct flight between Confins and Guarulhos, São Paulo (SBGR)? A direct flight is one with no intermediate stops.

In [9]:
# put your code here
'SBCF' in B.neighbors('SBGR')

True

# EXERCISE 2

If I wanted to fly from Confins to Guarulhos, São Paulo what would be an itinerary with the fewest number of flights?

In [10]:
# put your code here
nx.shortest_path(B, 'SBCF', 'SBGR')

['SBCF', 'SBGR']

# EXERCISE 3

Is it possible to travel from any airport in the Brazil to any other airport in the Brazil, possibly using connecting flights? In other words, does there exist a path in the network between every possible pair of airports?

In [11]:
# put your code here
nx.is_connected(B)

False

# Display airports map
Now we could see the brazilian airlines.

In [12]:
import folium

For a better visualization, we represent the difference of the airlines flights in the thickness of lines in the graph.

In [13]:
# Sort weights
edges_weight = sorted(B.edges(data=True), key= lambda edge: edge[2]['flight_count'], reverse=True)

# Get maximum weight
max_weight = edges_weight[0][2]['flight_count']

# Binds
quartile_1 = max_weight * 0.1
quartile_2 = max_weight * 0.2
quartile_3 = max_weight * 0.4

In [14]:
def weight_line(weight):
  if weight < quartile_1:
    return 0.1
  if weight < quartile_2:
    return 0.1
  if weight < quartile_3:
    return 1
  
  return 3

In [15]:
# Create map
map = folium.Map(
    location=[-5.826592, -35.212558],
    zoom_start=3,
    tiles='OpenStreetMap'
)

# Adds nodes
for code in B.nodes():
    node = B.nodes()[code]
    
    folium.Circle([node['latitude'], node['longitude']],
                  popup='<i>' + node['name'] + '</i>',
                  tooltip=code,
                  radius=10).add_to(map)

# Adds edges
for edge in B.edges(data=True):
    node_first = B.nodes[edge[0]]
    node_second = B.nodes[edge[1]]
    loc = [
        (node_first['latitude'], node_first['longitude']),
        (node_second['latitude'], node_second['longitude']),
    ]

    folium.PolyLine(loc,
                    color='red',
                    weight=weight_line(edge[2]['flight_count']),
                    opacity=0.6).add_to(map)

# Display map
map